# Forecasting COVID-19 with the DA-RNN (vanilla model)

In [ ]:
from google.colab import auth
from datetime import datetime
import os
auth.authenticate_user()
!git clone https://github.com/AIStream-Peelout/flow-forecast.git -b frozen_lay

Cloning into 'flow-forecast'...
remote: Enumerating objects: 16788, done.
remote: Counting objects: 100% (3645/3645), done.
remote: Compressing objects: 100% (1378/1378), done.
remote: Total 16788 (delta 2561), reused 3247 (delta 2246), pack-reused 13143
Receiving objects: 100% (16788/16788), 4.49 MiB | 14.93 MiB/s, done.
Resolving deltas: 100% (12112/12112), done.


In [ ]:
!gsutil cp -r gs://coronaviruspublicdata/covid_vax .

Copying gs://coronaviruspublicdata/covid_vax/clark_countyk.csv...
Copying gs://coronaviruspublicdata/covid_vax/grand_county.csv...
Copying gs://coronaviruspublicdata/covid_vax/miami_vax.csv...
Copying gs://coronaviruspublicdata/covid_vax/norfolk.csv...
/ [4 files][497.0 KiB/497.0 KiB]                                                
==> NOTE: You are performing a sequence of gsutil operations that may
run significantly faster if you instead use gsutil -m cp ... Please
see the -m section under "gsutil help options" for further information
about when gsutil -m can be advantageous.

Copying gs://coronaviruspublicdata/covid_vax/vax.csv...
/ [5 files][410.5 MiB/410.5 MiB]                                                
Operation completed over 5 objects/410.5 MiB.                                    


In [ ]:
def make_config_file(file_path, df_len, weight_path=None):
  run = wandb.init(project="covid_forecast_vax", entity="covid")
  wandb_config = wandb.config
  train_number = df_len*.6
  validation_number = df_len *.9
  config_default={                 
    "model_name": "DARNN",
    "model_type": "PyTorch",
    "model_params": {
        "n_time_series":11,
        "forecast_history":wandb_config["forecast_history"],
        "hidden_size_encoder":wandb_config["hidden_encoder"],
        "decoder_hidden_size": wandb_config["hidden_decoder"],
        "out_feats": 1,
        "gru_lstm": False
    },
    "dataset_params":
    {  "class": "default",
       "training_path": file_path,
       "validation_path": file_path,
       "test_path": file_path,
       "forecast_test_len":14,
       "batch_size":wandb_config["batch_size"],
       "forecast_history":wandb_config["forecast_history"]-1,
       "forecast_length":wandb_config["out_seq_length"],
       "train_end": int(train_number),
       "valid_start":int(train_number+1),
       "valid_end": int(validation_number),
       "test_start":int(train_number+1),
       "target_col": ["rolling_7_cases"],
       "relevant_cols": ["rolling_7_cases", "mobility_retail_recreation",	"mobility_grocery_pharmacy",	"mobility_parks",	"mobility_transit_stations",	"mobility_workplaces",	"mobility_residential", "Series_Complete_Pop_Pct"],
       "scaler": "StandardScaler", 
       "interpolate": False,
       "sort_column": "datetime",
       "feature_param":
        {
            "datetime_params":{
                "month": "numerical",
                "day": "numerical",
                "day_of_week": "numerical",
            }
        }
     
    },
    "training_params":
    {
       "criterion":"MSE",
       "optimizer": "Adam",
       "optim_params":
       {
           "lr": wandb_config["lr"],
       },
       "epochs": 10,
       "batch_size":wandb_config["batch_size"]
    
    },
    "GCS": True,
    "early_stopping":
    {
        "patience":3
    },
    "sweep":True,
    "wandb":False,
    "forward_params":{},
   "metrics":["MSE"],
   "inference_params":
   {     
         "datetime_start":"2021-10-19",
          "hours_to_forecast":16, 
          "num_prediction_samples": 100,
          "test_csv_path":file_path,
          "decoder_params":{
              "decoder_function": "simple_decode", 
            "unsqueeze_dim": 1
          },
          "dataset_params":{
             "file_path": file_path,
             "sort_column": "datetime",
             "forecast_history":wandb_config["forecast_history"]-1,
             "forecast_length":wandb_config["out_seq_length"],
             "relevant_cols": ["rolling_7_cases", "mobility_retail_recreation",	"mobility_grocery_pharmacy",	"mobility_parks",	"mobility_transit_stations",	"mobility_workplaces",	"mobility_residential", "Series_Complete_Pop_Pct"],
             "target_col": ["rolling_7_cases"],
             "scaling": "StandardScaler",
             "interpolate_param": False,
             "feature_params":
            {
            "datetime_params":{
                "month": "numerical",
                "day": "numerical",
                "day_of_week": "numerical",
            }
          }
      }
  }}
  if weight_path: 
    config_default["weight_path"] = weight_path
  wandb.config.update(config_default)
  return config_default

wandb_sweep_config_full = {
  "name": "Default sweep",
  "method": "grid",
  "parameters": {
        "batch_size": {
            "values": [10, 25, 30]
        },
        "lr":{
            "values":[0.001, 0.0001, .01, .1]
        },
        "forecast_history":{
            "values":[5, 10, 11, 15]
        },
        "out_seq_length":{
            "values":[1]
        },
        "hidden_encoder":
        {
            "values":[32, 64, 128]
        },
        "hidden_decoder":
        {
            "values":[32, 64, 128]
        }
  
    }
}

In [ ]:
import pandas as pd
def format_training_df(file_path: pd.DataFrame):
  df = pd.read_csv(file_path)
  df["Series_Complete_Pop_Pct"] = df["Series_Complete_Pop_Pct"].fillna(0)
  df["datetime"] = df["date"]
  df["new_cases"] = df["cases"].diff()
  df["rolling_7_cases"] = df["new_cases"].rolling(7, win_type='triang').mean()
  # df["rolling_7_deaths"] = df["deaths"].rolling(7, win_type='triang').mean()
  return df

In [ ]:
df = format_training_df("/content/covid_vax/miami_vax.csv")[10:]
df.to_csv("train_miami_vax.csv")

In [ ]:
df[["rolling_7_cases", "mobility_retail_recreation",	"mobility_grocery_pharmacy",	"mobility_parks",	"mobility_transit_stations",	"mobility_workplaces",	"mobility_residential", "Series_Complete_Pop_Pct"]]

rolling_7_cases  ...  Series_Complete_Pop_Pct
0                NaN  ...                      0.0
1                NaN  ...                      0.0
2                NaN  ...                      0.0
3                NaN  ...                      0.0
4                NaN  ...                      0.0
..               ...  ...                      ...
630            237.0  ...                      0.0
631            355.5  ...                      0.0
632            474.0  ...                      0.0
633            355.5  ...                      0.0
634            237.0  ...                      0.0

[635 rows x 8 columns]

In [ ]:
import os
os.chdir('flow-forecast')
!pip install -r  requirements.txt
!python setup.py develop
!mkdir data

     |████████████████████████████████| 371 kB 5.1 MB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 22.3 MB 1.2 MB/s 
     |████████████████████████████████| 5.8 MB 36.2 MB/s 
     |████████████████████████████████| 1.7 MB 45.0 MB/s 
     |████████████████████████████████| 20.6 MB 1.4 MB/s 
     |████████████████████████████████| 503 kB 69.2 MB/s 
     |████████████████████████████████| 816 kB 70.7 MB/s 
     |████████████████████████████████| 15.3 MB 26 kB/s 
     |████████████████████████████████| 1.0 MB 49.0 MB/s 
     |████████████████████████████████| 2.8 MB 28.7 MB/s 
     |████████████████████████████████| 180 kB 58.5 MB/s 
     |████████████████████████████████| 139 kB 52.3 MB/s 
     |████████████████████████████████| 97 kB 5.9 MB/s 
     |████████████████████████████████| 63 kB 1.5 MB/s 
     |████████████████████████████████| 575 kB 62.6 MB/s 
     |████

/usr/local/lib/python3.7/dist-packages/setuptools/dist.py:487: UserWarning: Normalizing '1.0.0dev' to '1.0.0.dev0'
  warnings.warn(tmpl.format(**locals()))
running develop
running egg_info
creating flood_forecast.egg-info
writing flood_forecast.egg-info/PKG-INFO
writing dependency_links to flood_forecast.egg-info/dependency_links.txt
writing requirements to flood_forecast.egg-info/requires.txt
writing top-level names to flood_forecast.egg-info/top_level.txt
writing manifest file 'flood_forecast.egg-info/SOURCES.txt'
package init file 'flood_forecast/__init__.py' not found (or not a regular file)
package init file 'flood_forecast/transformer_xl/__init__.py' not found (or not a regular file)
package init file 'flood_forecast/preprocessing/__init__.py' not found (or not a regular file)
package init file 'flood_forecast/da_rnn/__init__.py' not found (or not a regular file)
package init file 'flood_forecast/basic/__init__.py' not found (or not a regular file)
package init file 'flood_foreca

In [ ]:
!wandb login
os.environ['MODEL_BUCKET'] = "coronaviruspublicdata"
os.environ["ENVIRONMENT_GCP"] = "Colab"
os.environ["GCP_PROJECT"] = "gmap-997"

wandb: Currently logged in as: igodfried (use `wandb login --relogin` to force relogin)


In [ ]:
import wandb
sweep_full = wandb.sweep(wandb_sweep_config_full, project="covid_2.0")
#sweep_id = "21i08e3p"
from flood_forecast.trainer import train_function
wandb.agent(sweep_full, lambda:train_function("PyTorch", make_config_file("train_miami_vax.csv", len(df))))


Create sweep with ID: 2zu3mse9
Sweep URL: https://wandb.ai/igodfried/covid_2.0/sweeps/2zu3mse9


wandb: Agent Starting Run: jwk45kzs with config:
wandb: 	batch_size: 10
wandb: 	forecast_history: 5
wandb: 	hidden_decoder: 32
wandb: 	hidden_encoder: 32
wandb: 	lr: 0.001
wandb: 	out_seq_length: 1
wandb: WARNING Ignored wandb.init() arg project when running a sweep
wandb: WARNING Ignored wandb.init() arg entity when running a sweep


interpolate should be below
Running code to add temporal features
Created datetime feature columns are: 
['month', 'day', 'day_of_week']
Now loading train_miami_vax.csv
scaling now
interpolate should be below
Running code to add temporal features
Created datetime feature columns are: 
['month', 'day', 'day_of_week']
Now loading train_miami_vax.csv
scaling now
interpolate should be below
Running code to add temporal features
Created datetime feature columns are: 
['month', 'day', 'day_of_week']
Now loading train_miami_vax.csv
scaling now
Using Wandb config:
{'batch_size': 10, 'forecast_history': 5, 'hidden_decoder': 32, 'hidden_encoder': 32, 'lr': 0.001, 'out_seq_length': 1, 'model_name': 'DARNN', 'model_type': 'PyTorch', 'model_params': {'n_time_series': 11, 'forecast_history': 5, 'hidden_size_encoder': 32, 'decoder_hidden_size': 32, 'out_feats': 1, 'gru_lstm': False}, 'dataset_params': {'class': 'default', 'training_path': 'train_miami_vax.csv', 'validation_path': 'train_miami_vax.csv

Using a non-full backward hook when the forward contains multiple autograd Nodes is deprecated and will be removed in future versions. This hook will be missing some grad_input. Please use register_full_backward_hook to get the documented behavior.
Using a non-full backward hook when outputs are generated by different autograd Nodes is deprecated and will be removed in future versions. This hook will be missing some grad_output. Please use register_full_backward_hook to get the documented behavior.
Named tensors and all their associated APIs are an experimental feature and subject to change. Please do not use them for anything important until they are released as stable. (Triggered internally at  ../c10/core/TensorImpl.h:1408.)
/usr/local/lib/python3.7/dist-packages/torch/nn/modules/module.py:1025: UserWarning:

Using a non-full backward hook when the forward contains multiple autograd Nodes is deprecated and will be removed in future versions. This hook will be missing some grad_input

plotting with CI now
Now plotting final plots


...

interpolate should be below
Running code to add temporal features
Created datetime feature columns are: 
['month', 'day', 'day_of_week']
Now loading train_miami_vax.csv
scaling now
interpolate should be below
Running code to add temporal features
Created datetime feature columns are: 
['month', 'day', 'day_of_week']
Now loading train_miami_vax.csv
scaling now
interpolate should be below
Running code to add temporal features
Created datetime feature columns are: 
['month', 'day', 'day_of_week']
Now loading train_miami_vax.csv
scaling now
Using Wandb config:
{'batch_size': 30, 'forecast_history': 15, 'hidden_decoder': 128, 'hidden_encoder': 32, 'lr': 0.001, 'out_seq_length': 1, 'model_name': 'DARNN', 'model_type': 'PyTorch', 'model_params': {'n_time_series': 11, 'forecast_history': 15, 'hidden_size_encoder': 32, 'decoder_hidden_size': 128, 'out_feats': 1, 'gru_lstm': False}, 'dataset_params': {'class': 'default', 'training_path': 'train_miami_vax.csv', 'validation_path': 'train_miami_vax

/usr/local/lib/python3.7/dist-packages/torch/nn/modules/module.py:1025: UserWarning:

Using a non-full backward hook when the forward contains multiple autograd Nodes is deprecated and will be removed in future versions. This hook will be missing some grad_input. Please use register_full_backward_hook to get the documented behavior.

/usr/local/lib/python3.7/dist-packages/torch/nn/modules/module.py:1015: UserWarning:

Using a non-full backward hook when outputs are generated by different autograd Nodes is deprecated and will be removed in future versions. This hook will be missing some grad_output. Please use register_full_backward_hook to get the documented behavior.



plotting with CI now
Now plotting final plots


wandb: Agent Starting Run: 49aim1dm with config:
wandb: 	batch_size: 30
wandb: 	forecast_history: 15
wandb: 	hidden_decoder: 128
wandb: 	hidden_encoder: 32
wandb: 	lr: 0.0001
wandb: 	out_seq_length: 1
wandb: WARNING Ignored wandb.init() arg project when running a sweep
wandb: WARNING Ignored wandb.init() arg entity when running a sweep


interpolate should be below
Running code to add temporal features
Created datetime feature columns are: 
['month', 'day', 'day_of_week']
Now loading train_miami_vax.csv
scaling now
interpolate should be below
Running code to add temporal features
Created datetime feature columns are: 
['month', 'day', 'day_of_week']
Now loading train_miami_vax.csv
scaling now
interpolate should be below
Running code to add temporal features
Created datetime feature columns are: 
['month', 'day', 'day_of_week']
Now loading train_miami_vax.csv
scaling now
Using Wandb config:
{'batch_size': 30, 'forecast_history': 15, 'hidden_decoder': 128, 'hidden_encoder': 32, 'lr': 0.0001, 'out_seq_length': 1, 'model_name': 'DARNN', 'model_type': 'PyTorch', 'model_params': {'n_time_series': 11, 'forecast_history': 15, 'hidden_size_encoder': 32, 'decoder_hidden_size': 128, 'out_feats': 1, 'gru_lstm': False}, 'dataset_params': {'class': 'default', 'training_path': 'train_miami_vax.csv', 'validation_path': 'train_miami_va

In [ ]:
def make_config_file(file_path, df_len, weight_path=None):
  run = wandb.init(project="covid_forecast_vax", entity="covid")
  wandb_config = wandb.config
  train_number = df_len*.6
  validation_number = df_len *.9
  config_default={                 
    "model_name": "DARNN",
    "model_type": "PyTorch",
    "model_params": {
        "n_time_series":8,
        "forecast_history":5,
        "hidden_size_encoder":32,
        "decoder_hidden_size": 32,
        "out_feats": 1,
        "gru_lstm": False
    },
    "dataset_params":
    {  "class": "default",
       "training_path": file_path,
       "validation_path": file_path,
       "test_path": file_path,
       "forecast_test_len":14,
       "batch_size":wandb_config["batch_size"],
       "forecast_history":wandb_config["forecast_history"]-1,
       "forecast_length":wandb_config["out_seq_length"],
       "train_end": int(train_number),
       "valid_start":int(train_number+1),
       "valid_end": int(validation_number),
       "test_start":int(train_number+1),
       "target_col": ["rolling_7"],
       "relevant_cols": ["rolling_7", "mobility_retail_recreation",	"mobility_grocery_pharmacy",	"mobility_parks",	"mobility_transit_stations",	"mobility_workplaces",	"mobility_residential", "Series_Complete_Pop_Pct"],
       "scaler": "StandardScaler", 
       "interpolate": False,
       "sort_clolumn": "datetime",
       "feature_param":
        {
            "datetime_params":{
                "month": "numerical",
                "day": "numerical",
                "day_of_week": "numerical",
            }
        }
     
    },
    "training_params":
    {
       "criterion":"MSE",
       "optimizer": "Adam",
       "optim_params":
       {
           "lr": wandb_config["lr"],
       },
       "epochs": 10,
       "batch_size":wandb_config["batch_size"]
    
    },
    "GCS": True,
    "early_stopping":
    {
        "patience":3
    },
    "sweep":True,
    "wandb":False,
    "forward_params":{},
   "metrics":["MSE"],
   "inference_params":
   {     
         "datetime_start":"2021-10-19",
          "hours_to_forecast":16, 
          "num_prediction_samples": 100,
          "test_csv_path":file_path,
          "decoder_params":{
              "decoder_function": "simple_decode", 
            "unsqueeze_dim": 1
          },
          "dataset_params":{
             "file_path": file_path,
             "sort_clolumn": "datetime",
             "forecast_history":5,
             "forecast_length":1,
             "relevant_cols": ["rolling_7", "mobility_retail_recreation",	"mobility_grocery_pharmacy",	"mobility_parks",	"mobility_transit_stations",	"mobility_workplaces",	"mobility_residential", "Series_Complete_Pop_Pct"],
             "target_col": ["rolling_7"],
             "scaling": "StandardScaler",
             "interpolate_param": False,
             "feature_params":
            {
            "datetime_params":{
                "month": "numerical",
                "day": "numerical",
                "day_of_week": "numerical",
            }
          }
      }
  }}
  if weight_path: 
    config_default["weight_path"] = weight_path
  wandb.config.update(config_default)
  return config_default

train_function("PyTorch", make_config_file(train_miami_vax.csv) )

TypeError: ignored